In [1]:
import pandas as pd 
import requests
from bs4 import BeautifulSoup, Tag
import re
from multiprocessing.dummy import Pool as ThreadPool 

In [2]:
df = pd.read_csv('dataframe.csv')

In [3]:
# Get only unique artist-tracks -> Don't scrape two or more times a song
df_no_dupl = df.drop_duplicates(subset = ["artist_track"]) 

In [4]:
print(df.shape)

(257717, 5)


In [5]:
print(df_no_dupl.shape)

(180961, 5)


In [6]:
def get_text_with_br(tag, result=''):
    
    for x in tag.contents:
        if isinstance(x, Tag):  # check if content is a tag
            if x.name == 'br':  # if tag is <br> append it as string
                result += str(x)
            else:  # for any other tag, recurse
                result = get_text_with_br(x, result)
        else:  # if content is NavigableString (string), append
            result += x
    
    return result

def scrape_info(artist_track):

    print(artist_track)
    result = ''
    url  = "https://genius.com/" + artist_track
    try:
        page = requests.get(url)
    except:
        return "NA", "NA", "NA",[] 
    
    #Check if the genius page exists 
    if page.status_code != 200:
        return "NA", "NA", "NA",[]    
    
    html = BeautifulSoup(page.text, 'html.parser') # Take page's html
    
    song_id = html.find('meta', {"property": "twitter:app:url:iphone"})['content'].replace('genius://songs/','')
    
    # Get album
    try:
        album = html.find('a', {"href": "#primary-album"}).get_text() 
    except:
        album = "NA"
    
    # Get date
    try:
        date = "NA"
        container = html.find_all('div', {"class": "HeaderMetadata__Section-sc-1p42fnf-7"})
        for element in container:
            if "Release" in element.get_text():
                date = element.get_text().replace("Release Date","")
    except:
        pass
        
    # Get lyrics
    try:
        lyrics = html.find('div', {"id": "annotation-portal-target"})
        result = get_text_with_br(lyrics).replace('<br/>','\n')
        result = result.replace("EmbedShare URLCopyEmbedCopyCancelHow to Format Lyrics:Type out all lyrics, even if it’s a chorus that’s repeated throughout the songThe Section Header button breaks up song sections. Highlight the text then click the linkUse Bold and Italics only to distinguish between different singers in the same verse.E.g. “Verse 1: Kanye West, Jay-Z, Both”Capitalize each lineTo move an annotation to different lyrics in the song, use the [...] menu to switch to referent editing mode","")
    except:
        result = "NA"
        
        
    # Get comments
    
    url  = "https://genius.com/api/songs/" + song_id + "/comments"
    try:
        comments_page = requests.get(url).json()
    except:
        return album, date, result,[] 
    comments = comments_page['response']['comments']
    #print(comments)
    comment_list = []
    
    for comment in comments:
        if (comment['anonymous_author'] == None):
            comment_author = comment['author']['name']
            comment_date = comment['created_at']
            comment_text = comment['body']['dom']['children']
    
            comment_list.append((comment_author,comment_date,comment_text,artist_track))    
    
    return album,date,result, comment_list

In [7]:
songs_info = []
comments_info = []

def scrape(artist_track):
    album,date,lyrics,comments = scrape_info(artist_track)
    songs_info.append((album,date,lyrics,artist_track))
    comments_info.append(comments)

In [ ]:
# Pool of thread used to scrape faster all the songs

p = ThreadPool(50)
p.map(scrape,df_no_dupl.artist_track)
p.terminate()
p.join()
    

Crosby-Stills-Nash-Helplessly-Hoping-lyricsBob-Marley-The-Wailers-Coming-In-From-the-Cold-lyricsIncendiary-Survival-lyrics
Bon-Iver-Holocene-lyrics
Jungle-Platoon-lyrics
OneRepublic-Love-Runs-Out-lyrics

Korpiklaani-Vodka-lyrics
Nazrey-Johani-Allahummasalli-Ala-lyricsPapa-Roach-To-Be-Loved-lyrics
Anthonello-de-Caserta-Beauté-parfaite-lyrics

Coldplay-Trouble-lyrics
ZZ-Top-Old-Man-lyrics

My-Morning-Jacket-The-Day-Is-Coming-lyricsThe-2-Bears-Be-Strong-lyricsBloc-Party-Hunting-For-Witches-lyrics

Pink-Floyd-Money-Live-At-The-Empire-Pool-Wembley-London-1974-2011-Remaster-lyrics

David-Bowie-Ziggy-Stardust-lyricsChromatics-A-Matter-of-Time-lyricsSoilwork-Epitome-lyrics
Movado-Weh-Dem-A-Do-lyrics

Pearl-Jam-Got-Some-lyrics
Lucybell-Dame-Calma-lyrics
Factory-Floor-Work-Out-lyricsB-B-King-Ask-Me-No-Questions-lyrics
Linkin-Park-Runaway-lyrics
Nine-Inch-Nails-999999-lyrics
Nonpoint-Temper-lyrics
The-Dead-60s-Control-This-lyrics
The-Zombies-Time-of-the-Season-lyrics
Zombie-Nation-The-Fact-lyrics

Travis-Coming-Around-lyrics
James-Horner-You-dont-dream-in-cryo-lyrics
Ibrahim-Ferrer-El-Platanal-de-Bartolo-lyrics
The-Strokes-On-The-Other-Side-lyrics
Nick-Cave-The-Bad-Seeds-Where-the-Wild-Roses-Grow-with-Kylie-Minogue-lyrics
Ivan-Alyosha-The-Fold-lyrics
Bastille-Daniel-in-the-Den-lyrics
Eric-Clapton-The-Folks-Who-Live-On-The-Hill-lyrics
Mel-A-Dos-Palmos-del-Cielo-lyrics
Keira-Knightley-Tell-Me-If-You-Wanna-Go-Home-lyrics
The-Specials-Why-Edit-lyrics
Fayann-Lyons-Miss-Behave-lyrics
Bahamas-All-The-Time-lyrics
Mango-Beat-Mon-Amour-lyrics
Café-Tacvba-La-Pinta-lyrics
Nightmares-On-Wax-What-Im-Feeling-Rae-Christian-Mix-lyrics
The-Ready-Set-The-Ghost-Of-Los-Angeles-lyrics
Say-Yes-Dog-A-Friend-lyrics
Deez-Nuts-Yesterday-lyrics
Los-Pericos-Monaco-GP-lyrics
Glenn-Gould-Goldberg-Variations-BWV-988-Variation-18-a-1-Clav-Canone-alla-Sesta-1981-Version-lyrics
Bat-For-Lashes-Prescilla-lyrics
Ja-Tho-Dire-Així-I-Tot-lyrics
Ozzy-Osbourne-Diary-Of-A-Madman-lyrics
Michael-Jackson-Black-Or-White-Singl

The-Wombats-1996-lyrics
CHIC-Good-Times-2006-Remastered-Version-Original-12-Mix-lyrics
Nacha-Pop-Nadie-Puede-Parar-Live-lyricsMadison-Affair-Rainbow-lyrics

Aerosmith-Girls-of-Summer-lyrics
Franz-Ferdinand-Live-Alone-lyrics
Majesty-Heavy-Metal-Desire-lyrics
Bob-Marley-The-Wailers-Is-This-Love-lyrics
Extremoduro-Abreme-El-Pecho-Y-Registra-lyrics
Watoto-Childrens-Choir-Baraka-za-Mungu-lyrics
Passenger-A-Thousand-Matches-feat-Gbmqn1500003-lyrics
Vitamin-String-Quartet-DANCE-String-Quartet-Tribute-to-Justice-lyrics
Caspar-Babypants-Jason-Vontver-Be-Quiet-Mike-lyrics
Wanda-Jackson-Funnel-of-Love-lyrics
Robbie-Williams-Rock-DJ-lyrics
DJ-Fuzz-Ikrar-feat-Altimet-lyrics
The-Automatic-Lost-At-Home-lyrics
Dave-Matthews-Up-and-Away-lyrics
Silverstein-If-You-Could-See-Into-My-Soul-lyrics
The-Kooks-See-the-World-lyrics
Badly-Drawn-Boy-Camping-Next-To-Water-lyrics
Trey-Songz-Dive-In-lyrics
Stereophonics-Dakota-lyrics
Nacha-Pop-Sentado-Al-Borde-De-Ti-lyrics
Gianni-Bella-No-lyrics
Skism-Rave-Review-lyr

Tony-Allen-The-Champs-Night-Owl-Birds-lyrics
Ultra-Bra-Hauki-lyrics
Ice-Cube-It-Was-A-Good-Day-RemixEdited-lyrics
The-Police-Spirits-In-The-Material-World-lyrics
The-Swan-Silvertones-Oh-Mary-Dont-You-Mary-lyrics
Friday-Night-Fever-Sweet-Talk-lyrics
The-Honeybears-One-Bad-Stud-Number-One-lyrics
As-Alice-Sleeps-The-Dreamer-lyrics
Flight-Facilities-Two-Bodies-lyrics
Sareem-Poems-Shes-So-So-lyrics
Freeform-Five-Leviathan-Radio-Edit-lyrics
Hallucinogen-Dark-Persuasion-lyrics
Ben-Kweller-I-Need-You-Back-lyrics
Death-Cab-for-Cutie-State-Street-Residential-lyrics
Duck-Sauce-Radio-Stereo-Bingo-Players-Remix-lyrics
Jana-Kramer-I-Wont-Give-Up-lyrics
Shpongle-Electroplasm-lyrics
Bury-Tomorrow-The-Maiden-lyrics
Don-Henley-Through-Your-Hands-lyrics
The-Killers-My-List-lyrics
Pariisin-Kevät-Tämän-kylän-poikii-lyrics
Hallucinogen-Gamma-Goblins-Its-Turtles-All-the-Way-Down-Mix-lyrics
We-Came-As-Romans-Shapes-lyrics
Oddisee-The-Blooming-lyrics
Red-Hot-Chili-Peppers-Instrumental-1-lyrics
OneRepublic-Made

Slum-Village-Climax-lyrics
Arctic-Monkeys-Scummy-lyrics
Public-Enemy-He-Got-Game-From-The-He-Got-Game-Soundtrack-lyrics
Dashboard-Confessional-The-Places-You-Have-Come-To-Fear-The-Most-lyrics
Mayday-Parade-When-I-Get-Home-Youre-So-Dead-lyrics
The-Raconteurs-Salute-Your-Solution-lyrics
Rosana-Llegaremos-a-tiempo-lyrics
A-Tribe-Called-Quest-Vivrant-Thing-lyrics
Parkway-Drive-The-Siren-Song-Live-lyrics
The-Vaccines-Do-You-Want-a-Man-lyrics
Trail-Of-Tears-In-The-Valley-Of-Ashes-lyrics
Strung-Out-Too-Close-To-See-lyrics
Adam-Lambert-If-I-Had-You-lyrics
Jhameel-Shadow-of-a-Man-lyrics
Def-Con-Dos-Mi-reino-por-un-poco-de-caballo-lyrics
Itzhak-Perlman-Sonatas-and-Partitas-Partita-No-1-in-B-Minor-BWV-1002-Allemanda-lyrics
The-Virgins-Love-Is-Colder-Than-Death-lyrics
James-Vincent-McMorrow-Ghosts-lyrics
Thirty-Seconds-To-Mars-End-Of-All-Days-lyrics
White-Denim-Pretty-Green-lyrics
Lana-Del-Rey-Without-You-lyrics
Butch-Walker-Maybe-Its-Just-Me-lyrics
Carousels-Call-Along-the-Coast-lyrics
Birdy-Stan

...

The-Aqua-Velvets-Smoking-Panatelas-On-The-Blue-Mediterranean-Sea-lyrics
Blue-Metheny-Im-Calling-Out-No-Coldplay-On-The-Beach-Dub-lyrics
Burt-Bacharach-Walk-The-Way-You-Talk-lyrics
The-Tossers-Chelsea-Girls-lyrics
Busta-Rhymes-Touch-It-RemixFeaturing-DMX-Explicit-lyrics
Sanctus-Real-Lead-Me-lyrics
Paul-Baloche-Hosanna-Praise-Is-Rising-lyrics
Lester-Flatt-A-Boy-Named-Sue-lyrics
The-Rock-Heroes-Moses-Made-Famous-by-Coldplay-lyrics
Eyes-Burn-Electric-Aha-lyrics
Yes-Tempus-Fugit-2008-Remastered-LP-Version-lyrics
Stars-Time-Can-Never-Kill-The-True-Heart-lyrics
Lunasect-How-To-Disappear-Completely-And-Not-Be-Found-lyrics
Grass-Widow-Time-Could-Bend-lyrics
DePhazz-Something-Special-lyrics
Natalie-Imbruglia-Instant-Crush-Radio-Edit-Bonus-Track-lyrics
Piano-For-The-Soul-Talk-lyrics
Slowdive-Spanish-Air-lyrics
Joe-Cocker-Up-Where-We-Belong-with-Maxine-Green-Live-lyrics
Krakovia-Were-Born-In-Your-City-lyrics
Atreyu-Blow-lyrics
The-Donkeys-Please-Please-Me-Live-lyrics
Vanaprasta-Healthy-Geometry-ly

Paul-McCartney-Hey-Diddle-Dixon-Van-Winkle-Mix-2012-Master-lyrics
The-Mighty-Wah-The-Story-Of-The-Blues-Part-1-lyrics
George-Clinton-and-Prince-We-Can-Funk-lyrics
Queen-We-Will-Rock-You-Live-lyrics
Megaherz-Jagdzeit-Blitzkid-Gunnaraposs-Predator-Remix-lyrics
Van-Halen-Jump-Remastered-Live-Version-lyrics
Dr-Dog-Control-Yourself-lyrics
Mattia-Cupelli-We-Are-the-Avengers-lyrics
Elephanz-Stereo-lyrics
Fragma-Tocas-Miracle-Radio-Cut-lyrics
Kent-Just-Like-Money-lyrics
lostprophets-Bring-Em-Down-lyrics
Bruce-Robison-What-Would-Willie-Do-lyrics
Spice-Girls-Too-Much-lyrics
Tiziano-Ferro-Deslizas-Otra-Vez-lyrics
The-Gourds-You-Must-Not-Know-lyrics
Slade-Cum-On-Feel-The-Noize-lyrics
Television-Untitled-Instrumental-Previously-Unissued-lyrics
Arkania-La-bestia-dormida-lyrics
Money-Mark-Use-A-Sua-Cabeca-lyrics
Gilbert-Becaud-Le-mur-Olympia-1988-lyrics
Abyss-Judge-Shadows-lyrics
Bob-Marley-The-Wailers-Jamming-US-Version-lyrics
Dr-Dog-Weekend-lyrics
The-Haggis-Horns-Way-Of-The-Haggis-lyrics
Frank-Sin

Gentleman-Celebration-lyrics
Human-Element-Everything-In-Between-Original-Mix-lyrics
The-Business-Guinness-Boys-lyrics
Joe-Purdy-California-Girl-lyrics
Susan-Tedeschi-Share-Your-Love-lyrics
Rufus-T-Firefly-Ruidos-y-sueños-lyrics
Joe-Budden-Only-Human-feat-Emanny-lyrics
Grouper-Wind-Return-lyrics
Tobacco-Face-Breakout-lyrics
Joaquin-Sabina-El-Muro-De-Berlin-lyrics
The-Chieftains-Have-I-Told-You-Lately-That-I-Love-You-lyrics
Evergrey-The-Fire-lyrics
Von-Südenfed-Duckrog-lyrics
Zenzile-Scars-lyrics
Taylor-Davis-Dragon-Roost-Island-From-the-Wind-Waker-lyrics
Alex-Ubago-Maria-lyrics
Ghostface-Jellyfish-FeatTheodore-Unit-lyrics
REM-Living-Well-Is-The-Best-Revenge-lyrics
Andrés-Cepeda-Fallaste-lyrics
Joe-Purdy-Troubadour-lyrics
Beck-Walls-lyrics
Ghostface-Kilo-feat-Raekwon-lyrics
Groundation-Smile-lyrics
Patrick-Watson-Close-To-Paradise-lyrics
Second-On-an-island-lyrics
Neonfly-Spitting-Blood-lyrics
Winter-Parade-St-Johns-Asylum-lyrics
Casa-del-Mirto-Faces-lyrics
Bright-Eyes-Were-Going-to-Be-

Blå-Tåget-Staten-Och-Kapitalet-lyrics
Reba-McEntire-Ring-On-Her-Finger-Time-On-Her-Hands-lyrics
League-of-Legends-Get-Jinxed-lyrics
Bastards-On-Parade-Marys-Harpoon-LP-lyrics
Alaska-Y-Dinarama-Cómo-Pudiste-Hacerme-Esto-A-Mi-Carlos-Jean-Remix-lyrics
Rod-Stewart-Auld-Lang-Syne-lyrics
Stephanie-Ouragan-lyrics
Too-hort-Short-but-Funky-lyrics
Chon-Suda-lyrics
Sylver-Take-Me-Back-lyrics
TNutty-Strapped-Down-lyrics
Alaska-Y-Dinarama-Quiero-Ser-Chochi-lyrics
Laura-Pausini-Se-Fuè-lyrics
Freemasons-Rain-Down-Love-Walken-Extended-Mix-lyrics
Cachao-El-Fantasma-lyrics
Funkdoobiest-Bubble-Butts-lyrics
Q-And-Not-U-Line-In-the-Sand-lyrics
Yukmouth-We-Gone-Ride-lyrics
Wormrot-Ferocious-Bombardment-lyrics
Coldplay-Beautiful-World-lyrics
Alex-Ubago-Ciudad-desierta-lyrics
Ice-Cube-Ghetto-Vet-2007-Digital-Remaster-lyrics
Reba-McEntire-The-Fear-Of-Being-Alone-lyrics
Breakbot-Feat-Irfane-One-Out-Of-Two-feat-Irfane-lyrics
Beastie-Boys-ChChCheck-It-Out-lyrics
Valérie-Delgado-Only-Girl-In-The-World-lyrics
Rodri

Miranda-Lee-Richards-Early-November-lyrics
Grateful-Dead-Saint-Of-Circumstance-Live-at-Richmond-Coliseum-Richmond-VA-November-1-1985-lyrics
Buju-Banton-Ring-The-Alarm-lyrics
David-Bowie-The-Man-Who-Sold-the-World-Remastered-lyrics
Muchuu-Dancing-With-A-Ghost-lyrics
Filter-The-Best-Things-lyrics
Sébastien-Tellier-Universe-lyrics
Dick-Dale-and-his-DelTones-Surf-Beat-lyrics
Rosa-Leon-F-Perro-Salchicha-lyrics
Hanuman-One-Armed-Bandit-lyrics
Jackson-And-His-Computer-Band-Utopia-lyrics
Sarah-Blackwood-Mama-Open-your-eyes-lyrics
Emeralds-Double-Helix-lyrics
The-Doors-The-End-lyrics
Millencolin-Done-Is-Done-lyrics
The-Cast-Of-Cheers-Family-lyrics
Grupo-Encanto-Tachin-lyrics
Thievery-Corporation-Sound-the-Alarm-lyrics
Chris-Lennertz-Reflection-Score-lyrics
Reign-Supreme-And-Come-What-May-lyrics
Joshua-Radin-You-Got-Growin-Up-To-Do-feat-Patty-Griffin-lyrics
Foxy-Shazam-Its-Hair-Smelled-Like-Bonfire-lyrics
The-Shouting-Matches-Seven-Sisters-lyrics
Brain-Power-Unlimited-Floating-In-Space-lyrics
Ca

# MONGODB

In [9]:
# Getting all song names 

artists_tracks = []
for song in songs_info:
    artists_tracks.append(song[3])

In [22]:
df = df[df['artist_track'].isin(artists_tracks)] # Checking which song_names have been scraped 

In [23]:
print(df.shape)

(257717, 5)


In [30]:
df_songs_info = pd.DataFrame(songs_info,columns=['album','date','lyrics','artist_track']) # Create the dataframe for mongoDB info

In [31]:
df = pd.merge(df,df_songs_info,on='artist_track') # Merge the old info with the info scraped

In [32]:
df.drop_duplicates(subset=['artist_track']).head(30)

user_id                artist  \
0   9cc0cfd4d7d7885102480dd99e7a90d6    Crosby Stills Nash   
1   07f0fc3be95dcd878966b1f9572ff670                  C418   
2   07f0fc3be95dcd878966b1f9572ff670                  C418   
3   07f0fc3be95dcd878966b1f9572ff670         Pretty Lights   
4   07f0fc3be95dcd878966b1f9572ff670  Ludwig van Beethoven   
5   07f0fc3be95dcd878966b1f9572ff670               Ratatat   
7   07f0fc3be95dcd878966b1f9572ff670           The Prodigy   
10  07f0fc3be95dcd878966b1f9572ff670              Skrillex   
24  07f0fc3be95dcd878966b1f9572ff670            Shaka Ponk   
26  07f0fc3be95dcd878966b1f9572ff670       Dschinghis Khan   
27  07f0fc3be95dcd878966b1f9572ff670             Daft Punk   
29  07f0fc3be95dcd878966b1f9572ff670           Kenji Kawai   
30  07f0fc3be95dcd878966b1f9572ff670           Murray Gold   
32  07f0fc3be95dcd878966b1f9572ff670      Zalza vs Scattle   
33  07f0fc3be95dcd878966b1f9572ff670        Our Last Night   
35  07f0fc3be95dcd878966b1f9572ff670            Sex BobOmb   
36  07f0fc3be95dcd878966b1f9572ff670            Portishead   
46  07f0fc3be95dcd878966b1f9572ff670              Bon Jovi   
57  07f0fc3be95dcd878966b1f9572ff670                 Creed   
64  07f0fc3be95dcd878966b1f9572ff670            Pink Floyd   
70  07f0fc3be95dcd878966b1f9572ff670               Jurojin   
71  07f0fc3be95dcd878966b1f9572ff670         Birdy Nam Nam   
73  944c80d26922ae634d6ce445b1fdff7f       Various Artists   
74  944c80d26922ae634d6ce445b1fdff7f                 McFly   
75  944c80d26922ae634d6ce445b1fdff7f        Elise Lieberth   
76  944c80d26922ae634d6ce445b1fdff7f       The Courteeners   
77  944c80d26922ae634d6ce445b1fdff7f            Ben Howard   
83  944c80d26922ae634d6ce445b1fdff7f        Flogging Molly   
87  944c80d26922ae634d6ce445b1fdff7f             The Twang   
89  944c80d26922ae634d6ce445b1fdff7f          Lennon Maisy   

                                                track        playlist  \
0                                   Helplessly Hoping  HARD ROCK 2010   
1                                               Chris            C418   
2                                            Équinoxe            C418   
3                                    I Know the Truth       Chill out   
4   Sonata No 23 In F Minor Op 57 Appassionata Ass...       Classique   
5                                             Kennedy         Electro   
7                             Take Me To The Hospital         Electro   
10                               Bangarang feat Sirah          Soirée   
24                                          Lets Bang          Soirée   
26                                Moskau Long Version          Soirée   
27                                             Finale         Starred   
29                       M01 Making of Cyborg Chant I         Starred   
30                         Voyage of the Damned Suite         Starred   
32                                              Xycle         Starred   
33                                               Fate   Work playlist   
35                                      Garbage Truck   Work playlist   
36                                          Glory Box   Work playlist   
46                                        Its My Life   Work playlist   
57                                    One Last Breath   Work playlist   
64                    Shine On You Crazy Diamond Live   Work playlist   
70                                          The Scars   Work playlist   
71                             Trans Boulogne Express   Work playlist   
73                              I Fancy Laura Marling  2014 beginning   
74                  Love Is On The Radio Mr Mrs F Mix  2014 beginning   
75                                  She Keeps Me Warm  2014 beginning   
76                                 That Kiss Acoustic  2014 beginning   
77                                           Gracious        Gracious   
83                   If I Ever Leave This World Alive         

In [74]:
df.to_csv('playlist_info.csv',index = False) 

# GRAPHDB

In [38]:
print(comments_info[:200])

[[], [], [], [], [], [], [], [], [], [], [], [], [], [], [('DeeCee', 1403638235, [{'tag': 'p', 'children': ['We should embrace the contractions here! The “It is"s don’t fit with how the song is actually sung; Jacoby is clearly using "it’s”. And to me it sounds like he’s singing “I got” and “I’ve gotta” rather than “I have got” and “I have got to.”']}, '', {'tag': 'p', 'children': ['Arguably nitpicky, yep. :)']}], 'Papa-Roach-To-Be-Loved-lyrics'), ('CySorcerorD', 1494570401, [{'tag': 'p', 'children': ['replace the A with an I to correct the “A love deprevation” to “I love deprevation”']}], 'Papa-Roach-To-Be-Loved-lyrics'), ('guesg', 1620154841, [{'tag': 'p', 'children': ['I love that this song was the theme song for WWE raw from 2006- 2009.']}], 'Papa-Roach-To-Be-Loved-lyrics'), ('SpaceGhostBenoit', 1626561019, [{'tag': 'p', 'children': ['stayed up every school night as a kid just to watch cena edge and DX']}], 'Papa-Roach-To-Be-Loved-lyrics')], [], [('Meandmylife', 1408078858, [{'tag':

In [39]:
comment_list = [x for x in comments_info if x] #remove [] lists 

In [40]:
comments_list_flat = [item for sublist in comment_list for item in sublist] # Transform list of list in a list

In [70]:
new_comment_list = []

for cm in comments_list_flat:
    #print(cm)
    txt = ''
    for tag in cm[2]:
        if (type(tag) is dict and tag['tag'] == 'p'):
            if ('children' in tag):
                for words in tag['children']:
                    if(type(words) is dict):
                        txt += '\n'
                    else:
                        txt = txt + words + ' '       
    new_comment_list.append((cm[0],cm[1],txt,cm[3]))

In [72]:
df_comment_info = pd.DataFrame(new_comment_list,columns=['author','date','comment','artist_track'])

In [75]:
df_comment_info.to_csv('comments_info.csv',index = False)